<a href="https://colab.research.google.com/github/BooEiEi/project/blob/main/waist_to_hip_radio.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
import pandas as pd #นำเข้า pandas แทนที่ด้วย pd
import os# os ใช้จัดการกับไฟล์ ว่าอยู่ที่ไหน
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt
from google.colab import drive #นำเข้าข้อมูลจาก drive
drive.mount('/content/drive')
path = '/content/drive/My Drive/project'# ชี้ dirve ที่เราต้องการ
import missingno as mno
import missingno as msno
from sklearn import linear_model
%matplotlib inline
import matplotlib
import sklearn 
from sklearn.impute import KNNImputer
from sklearn.metrics import mean_squared_error
import time

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [2]:
data = pd.read_csv(os.path.join(path, 'DFforCreateNaN.csv'))
data = data.drop(['Unnamed: 0'], axis=1)
data

Sex  AgeSYear  Weight  Height   BMI  Systolic  Diastolic  HeartRate  \
0      2      57.0    47.4   153.0  20.2     114.0       75.0       69.0   
1      2      24.0    53.2   157.0  21.6     103.0       69.0       78.0   
2      2      62.0    54.4   165.0  20.0      95.0       75.0       83.0   
3      2      35.0    56.3   161.0  21.7      95.0       57.0       72.0   
4      1      46.0    72.3   170.0  25.0     133.0       77.0      107.0   
..   ...       ...     ...     ...   ...       ...        ...        ...   
148    1      60.0    72.0   170.0  24.9     131.0       74.0       69.0   
149    1      58.0    62.0   168.0  22.0     103.0       76.0       72.0   
150    2      42.0    55.5   165.0  20.4     102.0       52.0       77.0   
151    2      61.0    61.8   159.0  24.4     117.0       60.0       72.0   
152    2      31.0    58.2   169.0  20.4     108.0       69.0       73.0   

      SMM  Fat Mass  ...  003_Creatinine  004_Uric Acid  005_Cholesterol  \
0    19.3      12.5  ...             1.0            5.0            176.0   
1    21.3      14.6  ...             0.8            5.2            159.0   
2    21.6      15.2  ...             0.7            4.1            230.0   
3    22.5      15.4  ...             0.6            5.0            198.0   
4    29.2      19.0  ...             0.9            6.9            194.0   
..    ...       ...  ...             ...            ...              ...   
148  30.5      13.8  ...             0.9            6.9            182.0   
149  27.8      11.9  ...             1.0            6.8            191.0   
150  22.9      14.1  ...             0.8            4.7            212.0   
151  23.4      19.2  ...             0.8            5.1            235.0   
152  25.0      13.0  ...             0.7            4.3            200.0   

     006_Triglyceride  008_HDL-C  009_LDL  010_AST  012_ALT  \
0                51.0       72.0     94.0     16.0     16.0   
1                45.0       52.0     98.0     13.0     17.0   
2                94.0       61.0    151.0     18.0     31.0   
3                47.0       68.0    120.0     16.0     20.0   
4                63.0       60.0    122.0     15.0     19.0   
..                ...        ...      ...      ...      ...   
148             179.0       39.0    107.0     36.0     31.0   
149              62.0       47.0    132.0     16.0     33.0   
150              68.0       63.0    135.0     11.0     16.0   
151              66.0       56.0    166.0     15.0     23.0   
152              44.0       56.0    135.0     14.0     21.0   

     013_Alkaline Phos  071_HbA1c  
0                 62.0        5.1  
1                 50.0        5.4  
2                 76.0        5.6  
3                 35.0        5.1  
4                 69.0        5.2  
..                 ...        ...  
148               79.0        6.5  
149               42.0        6.8  
150               33.0        4.8  
151               44.0        5.4  
152               31.0        4.7  

[153 rows x 26 columns]

# 10 % random nan 

In [3]:
t_start = time.time()
for i in range(1,1001):
  globals()[f'waist_to_hip_radio1{i}'] = data.copy() # for loop variable name
  np.random.seed(i) # for loop seed
  n = int((153*10/100)) 
  index_nan = np.random.choice(globals()[f'waist_to_hip_radio1{i}']['waist to hip radio'].size, n, replace=False)
  globals()[f'waist_to_hip_radio1{i}']['waist to hip radio'].ravel()[index_nan] = np.nan
t_end = time.time()
print(f'เวลาที่ใช้ในการประมวลผล {t_end- t_start} วินาที')
print(f'เวลาที่ใช้ในการประมวลผล {(t_end- t_start)/60} นาที')

เวลาที่ใช้ในการประมวลผล 0.22024917602539062 วินาที
เวลาที่ใช้ในการประมวลผล 0.003670819600423177 นาที


## Imputation using Mean

In [4]:
from sklearn.impute import SimpleImputer

In [5]:
t_start = time.time()
mean10_imputer = SimpleImputer(strategy='mean')
for i in range(1,1001):
  globals()[f'imputed_mean10_{i}'] = mean10_imputer.fit_transform(globals()[f'waist_to_hip_radio1{i}'].copy()) #for loop miss forest impputation 
  globals()[f'MSE_MEAN10_{i}'] = mean_squared_error(data, globals()[f'imputed_mean10_{i}']) # for loop mean_squared_error
t_end = time.time()
t10_MEAN= (t_end- t_start)

In [6]:
t_start = time.time()
mse_mean10_total = 0 
MSE_MEAN10_1001 = 0
for i in range(1,1001):
  mse_mean10_total = mse_mean10_total + globals()[f'MSE_MEAN10_{i}']
AMSE_waist_to_hip_radio1_mean = mse_mean10_total/1000
print(f'AMSE_waist_to_hip_radio1_mean = {AMSE_waist_to_hip_radio1_mean}')
t_end = time.time()
print(f'เวลาที่ใช้ในการประมวลผล {t_end- t_start} วินาที')
print(f'เวลาที่ใช้ในการประมวลผล {(t_end- t_start)/60} นาที')

AMSE_waist_to_hip_radio1_mean = 1.8357502198607793e-05
เวลาที่ใช้ในการประมวลผล 0.0009908676147460938 วินาที
เวลาที่ใช้ในการประมวลผล 1.651446024576823e-05 นาที


## Imputation using the miss forest

In [7]:
import sys
import sklearn.neighbors._base
sys.modules['sklearn.neighbors.base'] = sklearn.neighbors._base
!pip install missingpy
import missingpy
from missingpy import MissForest
from sklearn.metrics import mean_squared_error

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [8]:
t_start = time.time()
MF10_imputer = MissForest()
for i in range(1,1001):
  globals()[f'imputed_mf10_{i}'] = MF10_imputer.fit_transform(globals()[f'waist_to_hip_radio1{i}'].copy()) #for loop miss forest impputation 
  globals()[f'MSE_MF10_{i}'] = mean_squared_error(data, globals()[f'imputed_mf10_{i}']) # for loop mean_squared_error
t_end = time.time()
t10_MF= (t_end- t_start)

/usr/local/lib/python3.8/dist-packages/sklearn/ensemble/_forest.py:396: FutureWarning: Criterion 'mse' was deprecated in v1.0 and will be removed in version 1.2. Use `criterion='squared_error'` which is equivalent.
  warn(
/usr/local/lib/python3.8/dist-packages/sklearn/ensemble/_forest.py:396: FutureWarning: Criterion 'mse' was deprecated in v1.0 and will be removed in version 1.2. Use `criterion='squared_error'` which is equivalent.
  warn(


Iteration: 0
Iteration: 1


/usr/local/lib/python3.8/dist-packages/sklearn/ensemble/_forest.py:396: FutureWarning: Criterion 'mse' was deprecated in v1.0 and will be removed in version 1.2. Use `criterion='squared_error'` which is equivalent.
  warn(
/usr/local/lib/python3.8/dist-packages/sklearn/ensemble/_forest.py:396: FutureWarning: Criterion 'mse' was deprecated in v1.0 and will be removed in version 1.2. Use `criterion='squared_error'` which is equivalent.
  warn(


Iteration: 2
Iteration: 0
Iteration: 1


/usr/local/lib/python3.8/dist-packages/sklearn/ensemble/_forest.py:396: FutureWarning: Criterion 'mse' was deprecated in v1.0 and will be removed in version 1.2. Use `criterion='squared_error'` which is equivalent.
  warn(
/usr/local/lib/python3.8/dist-packages/sklearn/ensemble/_forest.py:396: FutureWarning: Criterion 'mse' was deprecated in v1.0 and will be removed in version 1.2. Use `criterion='squared_error'` which is equivalent.
  warn(


...

Iteration: 2
Iteration: 3


/usr/local/lib/python3.8/dist-packages/sklearn/ensemble/_forest.py:396: FutureWarning: Criterion 'mse' was deprecated in v1.0 and will be removed in version 1.2. Use `criterion='squared_error'` which is equivalent.
  warn(


Iteration: 0
Iteration: 1


/usr/local/lib/python3.8/dist-packages/sklearn/ensemble/_forest.py:396: FutureWarning: Criterion 'mse' was deprecated in v1.0 and will be removed in version 1.2. Use `criterion='squared_error'` which is equivalent.
  warn(
/usr/local/lib/python3.8/dist-packages/sklearn/ensemble/_forest.py:396: FutureWarning: Criterion 'mse' was deprecated in v1.0 and will be removed in version 1.2. Use `criterion='squared_error'` which is equivalent.
  warn(


Iteration: 2


In [9]:
t_start = time.time()
mse_mf10_total = 0 
MSE_MF10_1001 = 0
for i in range(1,1001):
  mse_mf10_total = mse_mf10_total + globals()[f'MSE_MF10_{i}']
AMSE_waist_to_hip_radio1_mf = mse_mf10_total/1000
print(f'AMSE_waist_to_hip_radio1_mf = {AMSE_waist_to_hip_radio1_mf}')
t_end = time.time()
print(f'เวลาที่ใช้ในการประมวลผล {t_end- t_start} วินาที')
print(f'เวลาที่ใช้ในการประมวลผล {(t_end- t_start)/60} นาที')

AMSE_waist_to_hip_radio1_mf = 1.6394321694318829e-06
เวลาที่ใช้ในการประมวลผล 0.0010495185852050781 วินาที
เวลาที่ใช้ในการประมวลผล 1.7491976420084634e-05 นาที


## Imputation using the KNN

In [10]:
from sklearn import neighbors
from sklearn.impute import KNNImputer

In [13]:
t_start = time.time()
KNN10_imputer = KNNImputer(n_neighbors = 15)
for i in range(1,1001):
  globals()[f'imputed_KNN10_{i}'] = KNN10_imputer.fit_transform(globals()[f'waist_to_hip_radio1{i}'].copy())
  globals()[f'MSE_KNN10_{i}'] = mean_squared_error(data, globals()[f'imputed_KNN10_{i}'])
t_end = time.time()
t10_KNN= (t_end- t_start)

In [14]:
t_start = time.time()
mse_knn10_total = 0 
MSE_KNN10_1001 = 0
for i in range(1,1001):
  mse_knn10_total = mse_knn10_total + globals()[f'MSE_KNN10_{i}']
AMSE_waist_to_hip_radio1_knn = mse_knn10_total/1000
print(f'AMSE_waist_to_hip_radio1_knn = {AMSE_waist_to_hip_radio1_knn}')
t_end = time.time()
print(f'เวลาที่ใช้ในการประมวลผล {t_end- t_start} วินาที')
print(f'เวลาที่ใช้ในการประมวลผล {(t_end- t_start)/60} นาที')

AMSE_waist_to_hip_radio1_knn = 3.982333277470532e-06
เวลาที่ใช้ในการประมวลผล 0.0010440349578857422 วินาที
เวลาที่ใช้ในการประมวลผล 1.7400582631429037e-05 นาที


## Imputation using the MICE

In [15]:
from sklearn.experimental import enable_iterative_imputer
from sklearn.impute import IterativeImputer
from sklearn.linear_model import LinearRegression
from sklearn import svm

### LinearRegression model

In [ ]:
t_start = time.time()
lr = LinearRegression()
for i in range(1,1001):
  imp = IterativeImputer(estimator= lr , max_iter= 10, verbose=0, imputation_order='roman',initial_strategy = 'mean',random_state= i)
  globals()[f'imputed_lr10_{i}'] = imp.fit_transform(globals()[f'waist_to_hip_radio1{i}'].copy())
  globals()[f'MSE_lr10_{i}'] = mean_squared_error(data, globals()[f'imputed_lr10_{i}'])
t_end = time.time()
t10_LR= (t_end- t_start)

In [17]:
t_start = time.time()
mse_lr10_total = 0 
MSE_lr10_1001 = 0
for i in range(1,1001):
  mse_lr10_total = mse_lr10_total + globals()[f'MSE_lr10_{i}']
AMSE_waist_to_hip_radio1_lr = mse_lr10_total/1000
print(f'AMSE_waist_to_hip_radio1_lr = {AMSE_waist_to_hip_radio1_lr}')
t_end = time.time()
print(f'เวลาที่ใช้ในการประมวลผล {t_end- t_start} วินาที')
print(f'เวลาที่ใช้ในการประมวลผล {(t_end- t_start)/60} นาที')

AMSE_waist_to_hip_radio1_lr = 4.326282018648429e-06
เวลาที่ใช้ในการประมวลผล 0.0008020401000976562 วินาที
เวลาที่ใช้ในการประมวลผล 1.3367335001627605e-05 นาที


### Support Vector Machine model

In [ ]:
t_start = time.time()
regr = svm.SVR()
for i in range(1,1001):
  svm_svr = IterativeImputer(estimator= regr, max_iter= 10, verbose=0, imputation_order='roman',initial_strategy = 'mean',random_state= i)
  globals()[f'imputed_svm10_{i}'] = svm_svr.fit_transform(globals()[f'waist_to_hip_radio1{i}'].copy())
  globals()[f'MSE_svm10_{i}'] = mean_squared_error(data, globals()[f'imputed_svm10_{i}'])
t_end = time.time()
t10_SVM= (t_end- t_start)

In [19]:
t_start = time.time()
mse_svm10_total = 0 
MSE_svm10_1001 = 0
for i in range(1,1001):
  mse_svm10_total = mse_svm10_total + globals()[f'MSE_svm10_{i}']
AMSE_waist_to_hip_radio1_svm = mse_svm10_total/1000
print(f'AMSE_waist_to_hip_radio1_svm = {AMSE_waist_to_hip_radio1_svm}')
t_end = time.time()
print(f'เวลาที่ใช้ในการประมวลผล {t_end- t_start} วินาที')
print(f'เวลาที่ใช้ในการประมวลผล {(t_end- t_start)/60} นาที')

AMSE_waist_to_hip_radio1_svm = 8.358532508551501e-06
เวลาที่ใช้ในการประมวลผล 0.0012166500091552734 วินาที
เวลาที่ใช้ในการประมวลผล 2.027750015258789e-05 นาที


## Imputation using the EM

### impy.em

In [20]:
!pip install impyute
import impyute as impy

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [21]:
t_start = time.time()
for i in range(1,1001):
  globals()[f'imputed_impy10_{i}'] = impy.em(globals()[f'waist_to_hip_radio1{i}'].values.copy())
  globals()[f'MSE_impy10_{i}'] = mean_squared_error(data, globals()[f'imputed_impy10_{i}'])
t_end = time.time()
t10_EM= (t_end- t_start)

In [22]:
t_start = time.time()
mse_impy10_total = 0 
MSE_impy10_1001 = 0
for i in range(1,1001):
  mse_impy10_total = mse_impy10_total + globals()[f'MSE_impy10_{i}']
AMSE_waist_to_hip_radio1_impy = mse_impy10_total/1000
print(f'AMSE_waist_to_hip_radio1_impy = {AMSE_waist_to_hip_radio1_impy}')
t_end = time.time()
print(f'เวลาที่ใช้ในการประมวลผล {t_end- t_start} วินาที')
print(f'เวลาที่ใช้ในการประมวลผล {(t_end- t_start)/60} นาที')

AMSE_waist_to_hip_radio1_impy = 3.358671019761667e-05
เวลาที่ใช้ในการประมวลผล 0.0007917881011962891 วินาที
เวลาที่ใช้ในการประมวลผล 1.3196468353271485e-05 นาที


# 20 % random nan 

In [25]:
for i in range(1,1001):
  globals()[f'waist_to_hip_radio2{i}'] = data.copy() # for loop variable name
  np.random.seed(i) # for loop seed
  n = int((153*20/100)) 
  index_nan = np.random.choice(globals()[f'waist_to_hip_radio2{i}']['waist to hip radio'].size, n, replace=False)
  globals()[f'waist_to_hip_radio2{i}']['waist to hip radio'].ravel()[index_nan] = np.nan

## Imputation using Mean

In [26]:
from sklearn.impute import SimpleImputer

In [27]:
t_start = time.time()
mean20_imputer = SimpleImputer(strategy='mean')
for i in range(1,1001):
  globals()[f'imputed_mean20_{i}'] = mean10_imputer.fit_transform(globals()[f'waist_to_hip_radio2{i}'].copy()) #for loop miss forest impputation 
  globals()[f'MSE_MEAN20_{i}'] = mean_squared_error(data, globals()[f'imputed_mean20_{i}']) # for loop mean_squared_error
t_end = time.time()
t20_MEAN = (t_end- t_start)

In [28]:
t_start = time.time()
mse_mean20_total = 0 
MSE_MEAN20_1001 = 0
for i in range(1,1001):
  mse_mean20_total = mse_mean20_total + globals()[f'MSE_MEAN20_{i}']
AMSE_waist_to_hip_radio2_mean = mse_mean20_total/1000
print(f'AMSE_waist_to_hip_radio2_mean = {AMSE_waist_to_hip_radio2_mean}')
t_end = time.time()
print(f'เวลาที่ใช้ในการประมวลผล {t_end- t_start} วินาที')
print(f'เวลาที่ใช้ในการประมวลผล {(t_end- t_start)/60} นาที')

AMSE_waist_to_hip_radio2_mean = 3.6183069533634644e-05
เวลาที่ใช้ในการประมวลผล 0.0009028911590576172 วินาที
เวลาที่ใช้ในการประมวลผล 1.504818598429362e-05 นาที


## Imputation using the miss forest

In [29]:
import sys
import sklearn.neighbors._base
sys.modules['sklearn.neighbors.base'] = sklearn.neighbors._base
!pip install missingpy
import missingpy
from missingpy import MissForest
from sklearn.metrics import mean_squared_error

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [30]:
t_start = time.time()
MF20_imputer = MissForest()
for i in range(1,1001):
  globals()[f'imputed_mf20_{i}'] = MF20_imputer.fit_transform(globals()[f'waist_to_hip_radio2{i}'].copy()) #for loop miss forest impputation 
  globals()[f'MSE_MF20_{i}'] = mean_squared_error(data, globals()[f'imputed_mf20_{i}']) # for loop mean_squared_error
t_end = time.time()
t20_MF = (t_end- t_start)

/usr/local/lib/python3.8/dist-packages/sklearn/ensemble/_forest.py:396: FutureWarning: Criterion 'mse' was deprecated in v1.0 and will be removed in version 1.2. Use `criterion='squared_error'` which is equivalent.
  warn(
/usr/local/lib/python3.8/dist-packages/sklearn/ensemble/_forest.py:396: FutureWarning: Criterion 'mse' was deprecated in v1.0 and will be removed in version 1.2. Use `criterion='squared_error'` which is equivalent.
  warn(


Iteration: 0
Iteration: 1


/usr/local/lib/python3.8/dist-packages/sklearn/ensemble/_forest.py:396: FutureWarning: Criterion 'mse' was deprecated in v1.0 and will be removed in version 1.2. Use `criterion='squared_error'` which is equivalent.
  warn(
/usr/local/lib/python3.8/dist-packages/sklearn/ensemble/_forest.py:396: FutureWarning: Criterion 'mse' was deprecated in v1.0 and will be removed in version 1.2. Use `criterion='squared_error'` which is equivalent.
  warn(


Iteration: 2
Iteration: 0
Iteration: 1


/usr/local/lib/python3.8/dist-packages/sklearn/ensemble/_forest.py:396: FutureWarning: Criterion 'mse' was deprecated in v1.0 and will be removed in version 1.2. Use `criterion='squared_error'` which is equivalent.
  warn(
/usr/local/lib/python3.8/dist-packages/sklearn/ensemble/_forest.py:396: FutureWarning: Criterion 'mse' was deprecated in v1.0 and will be removed in version 1.2. Use `criterion='squared_error'` which is equivalent.
  warn(


...

/usr/local/lib/python3.8/dist-packages/sklearn/ensemble/_forest.py:396: FutureWarning: Criterion 'mse' was deprecated in v1.0 and will be removed in version 1.2. Use `criterion='squared_error'` which is equivalent.
  warn(
/usr/local/lib/python3.8/dist-packages/sklearn/ensemble/_forest.py:396: FutureWarning: Criterion 'mse' was deprecated in v1.0 and will be removed in version 1.2. Use `criterion='squared_error'` which is equivalent.
  warn(


Iteration: 2
Iteration: 3


/usr/local/lib/python3.8/dist-packages/sklearn/ensemble/_forest.py:396: FutureWarning: Criterion 'mse' was deprecated in v1.0 and will be removed in version 1.2. Use `criterion='squared_error'` which is equivalent.
  warn(


Iteration: 4
Iteration: 5


/usr/local/lib/python3.8/dist-packages/sklearn/ensemble/_forest.py:396: FutureWarning: Criterion 'mse' was deprecated in v1.0 and will be removed in version 1.2. Use `criterion='squared_error'` which is equivalent.
  warn(


In [31]:
t_start = time.time()
mse_mf20_total = 0 
MSE_MF20_1001 = 0
for i in range(1,1001):
  mse_mf20_total = mse_mf20_total + globals()[f'MSE_MF20_{i}']
AMSE_waist_to_hip_radio2_mf = mse_mf20_total/1000
print(f'AMSE_waist_to_hip_radio2_mf = {AMSE_waist_to_hip_radio2_mf}')
t_end = time.time()
print(f'เวลาที่ใช้ในการประมวลผล {t_end- t_start} วินาที')
print(f'เวลาที่ใช้ในการประมวลผล {(t_end- t_start)/60} นาที')

AMSE_waist_to_hip_radio2_mf = 3.357524084967327e-06
เวลาที่ใช้ในการประมวลผล 0.001018524169921875 วินาที
เวลาที่ใช้ในการประมวลผล 1.697540283203125e-05 นาที


## Imputation using the KNN

In [32]:
from sklearn import neighbors
from sklearn.impute import KNNImputer

In [33]:
t_start = time.time()
KNN20_imputer = KNNImputer(n_neighbors = 15)
for i in range(1,1001):
  globals()[f'imputed_KNN20_{i}'] = KNN10_imputer.fit_transform(globals()[f'waist_to_hip_radio2{i}'].copy())
  globals()[f'MSE_KNN20_{i}'] = mean_squared_error(data, globals()[f'imputed_KNN20_{i}'])
t_end = time.time()
t20_KNN = (t_end- t_start)

In [34]:
t_start = time.time()
mse_knn20_total = 0 
MSE_KNN20_1001 = 0
for i in range(1,1001):
  mse_knn20_total = mse_knn20_total + globals()[f'MSE_KNN20_{i}']
AMSE_waist_to_hip_radio2_knn = mse_knn20_total/1000
print(f'AMSE_waist_to_hip_radio2_knn = {AMSE_waist_to_hip_radio2_knn}')
t_end = time.time()
print(f'เวลาที่ใช้ในการประมวลผล {t_end- t_start} วินาที')
print(f'เวลาที่ใช้ในการประมวลผล {(t_end- t_start)/60} นาที')

AMSE_waist_to_hip_radio2_knn = 8.34682978604547e-06
เวลาที่ใช้ในการประมวลผล 0.0008721351623535156 วินาที
เวลาที่ใช้ในการประมวลผล 1.4535586039225261e-05 นาที


## Imputation using the MICE

In [35]:
from sklearn.experimental import enable_iterative_imputer
from sklearn.impute import IterativeImputer
from sklearn.linear_model import LinearRegression
from sklearn import svm

### LinearRegression model

In [ ]:
t_start = time.time()
lr = LinearRegression()
for i in range(1,1001):
  imp20 = IterativeImputer(estimator= lr , max_iter= 10, verbose=0, imputation_order='roman',initial_strategy = 'mean',random_state= i)
  globals()[f'imputed_lr20_{i}'] = imp20.fit_transform(globals()[f'waist_to_hip_radio2{i}'].copy())
  globals()[f'MSE_lr20_{i}'] = mean_squared_error(data, globals()[f'imputed_lr20_{i}'])
t_end = time.time()
t20_LR = (t_end- t_start)

In [37]:
t_start = time.time()
mse_lr20_total = 0 
MSE_lr20_1001 = 0
for i in range(1,1001):
  mse_lr20_total = mse_lr20_total + globals()[f'MSE_lr20_{i}']
AMSE_waist_to_hip_radio2_lr = mse_lr20_total/1000
print(f'AMSE_waist_to_hip_radio2_lr = {AMSE_waist_to_hip_radio2_lr}')
t_end = time.time()
print(f'เวลาที่ใช้ในการประมวลผล {t_end- t_start} วินาที')
print(f'เวลาที่ใช้ในการประมวลผล {(t_end- t_start)/60} นาที')

AMSE_waist_to_hip_radio2_lr = 1.0111337730767227e-05
เวลาที่ใช้ในการประมวลผล 0.0014581680297851562 วินาที
เวลาที่ใช้ในการประมวลผล 2.4302800496419272e-05 นาที


### Support Vector Machine model

In [ ]:
t_start = time.time()
regr = svm.SVR()
for i in range(1,1001):
  svm_svr = IterativeImputer(estimator= regr, max_iter= 10, verbose=0, imputation_order='roman',initial_strategy = 'mean',random_state= i)
  globals()[f'imputed_svm20_{i}'] = svm_svr.fit_transform(globals()[f'waist_to_hip_radio2{i}'].copy())
  globals()[f'MSE_svm20_{i}'] = mean_squared_error(data, globals()[f'imputed_svm20_{i}'])
t_end = time.time()
t20_SVM = (t_end- t_start)

In [39]:
t_start = time.time()
mse_svm20_total = 0 
MSE_svm20_1001 = 0
for i in range(1,1001):
  mse_svm20_total = mse_svm20_total + globals()[f'MSE_svm20_{i}']
AMSE_waist_to_hip_radio2_svm = mse_svm20_total/1000
print(f'AMSE_waist_to_hip_radio2_svm = {AMSE_waist_to_hip_radio2_svm}')
t_end = time.time()
print(f'เวลาที่ใช้ในการประมวลผล {t_end- t_start} วินาที')
print(f'เวลาที่ใช้ในการประมวลผล {(t_end- t_start)/60} นาที')

AMSE_waist_to_hip_radio2_svm = 1.701918102864713e-05
เวลาที่ใช้ในการประมวลผล 0.0009152889251708984 วินาที
เวลาที่ใช้ในการประมวลผล 1.5254815419514974e-05 นาที


## Imputation using the EM

### impy.em

In [40]:
!pip install impyute
import impyute as impy

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [41]:
t_start = time.time()
for i in range(1,1001):
  globals()[f'imputed_impy20_{i}'] = impy.em(globals()[f'waist_to_hip_radio2{i}'].values.copy())
  globals()[f'MSE_impy20_{i}'] = mean_squared_error(data, globals()[f'imputed_impy20_{i}'])
t_end = time.time()
t20_EM = (t_end- t_start)

In [42]:
t_start = time.time()
mse_impy20_total = 0 
MSE_impy20_1001 = 0
for i in range(1,1001):
  mse_impy20_total = mse_impy20_total + globals()[f'MSE_impy20_{i}']
AMSE_waist_to_hip_radio2_impy = mse_impy20_total/1000
print(f'AMSE_waist_to_hip_radio2_impy = {AMSE_waist_to_hip_radio2_impy}')
t_end = time.time()
print(f'เวลาที่ใช้ในการประมวลผล {t_end- t_start} วินาที')
print(f'เวลาที่ใช้ในการประมวลผล {(t_end- t_start)/60} นาที')

AMSE_waist_to_hip_radio2_impy = 6.760741414439194e-05
เวลาที่ใช้ในการประมวลผล 0.0010116100311279297 วินาที
เวลาที่ใช้ในการประมวลผล 1.6860167185465495e-05 นาที


# 30 % random nan 

In [43]:
for i in range(1,1001):
  globals()[f'waist_to_hip_radio3{i}'] = data.copy() # for loop variable name
  np.random.seed(i) # for loop seed
  n = int((153*30/100)) 
  index_nan = np.random.choice(globals()[f'waist_to_hip_radio3{i}']['waist to hip radio'].size, n, replace=False)
  globals()[f'waist_to_hip_radio3{i}']['waist to hip radio'].ravel()[index_nan] = np.nan

## Imputation using Mean

In [44]:
from sklearn.impute import SimpleImputer

In [45]:
t_start = time.time()
mean30_imputer = SimpleImputer(strategy='mean')
for i in range(1,1001):
  globals()[f'imputed_mean30_{i}'] = mean30_imputer.fit_transform(globals()[f'waist_to_hip_radio3{i}'].copy()) #for loop miss forest impputation 
  globals()[f'MSE_MEAN30_{i}'] = mean_squared_error(data, globals()[f'imputed_mean30_{i}']) # for loop mean_squared_error
t_end = time.time()
t30_MEAN = (t_end- t_start)

In [46]:
t_start = time.time()
mse_mean30_total = 0 
MSE_MEAN30_1001 = 0
for i in range(1,1001):
  mse_mean30_total = mse_mean30_total + globals()[f'MSE_MEAN30_{i}']
AMSE_waist_to_hip_radio3_mean = mse_mean30_total/1000
print(f'AMSE_waist_to_hip_radio3_mean = {AMSE_waist_to_hip_radio3_mean}')
t_end = time.time()
print(f'เวลาที่ใช้ในการประมวลผล {t_end- t_start} วินาที')
print(f'เวลาที่ใช้ในการประมวลผล {(t_end- t_start)/60} นาที')

AMSE_waist_to_hip_radio3_mean = 5.447352469834084e-05
เวลาที่ใช้ในการประมวลผล 0.0012798309326171875 วินาที
เวลาที่ใช้ในการประมวลผล 2.1330515543619792e-05 นาที


## Imputation using the miss forest

In [47]:
import sys
import sklearn.neighbors._base
sys.modules['sklearn.neighbors.base'] = sklearn.neighbors._base
!pip install missingpy
import missingpy
from missingpy import MissForest
from sklearn.metrics import mean_squared_error

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [48]:
t_start = time.time()
MF30_imputer = MissForest()
for i in range(1,1001):
  globals()[f'imputed_mf30_{i}'] = MF30_imputer.fit_transform(globals()[f'waist_to_hip_radio3{i}'].copy()) #for loop miss forest impputation 
  globals()[f'MSE_MF30_{i}'] = mean_squared_error(data, globals()[f'imputed_mf30_{i}']) # for loop mean_squared_error
t_end = time.time()
t30_MF = (t_end- t_start)

/usr/local/lib/python3.8/dist-packages/sklearn/ensemble/_forest.py:396: FutureWarning: Criterion 'mse' was deprecated in v1.0 and will be removed in version 1.2. Use `criterion='squared_error'` which is equivalent.
  warn(


Iteration: 0


/usr/local/lib/python3.8/dist-packages/sklearn/ensemble/_forest.py:396: FutureWarning: Criterion 'mse' was deprecated in v1.0 and will be removed in version 1.2. Use `criterion='squared_error'` which is equivalent.
  warn(
/usr/local/lib/python3.8/dist-packages/sklearn/ensemble/_forest.py:396: FutureWarning: Criterion 'mse' was deprecated in v1.0 and will be removed in version 1.2. Use `criterion='squared_error'` which is equivalent.
  warn(


Iteration: 1
Iteration: 2


/usr/local/lib/python3.8/dist-packages/sklearn/ensemble/_forest.py:396: FutureWarning: Criterion 'mse' was deprecated in v1.0 and will be removed in version 1.2. Use `criterion='squared_error'` which is equivalent.
  warn(


...

/usr/local/lib/python3.8/dist-packages/sklearn/ensemble/_forest.py:396: FutureWarning: Criterion 'mse' was deprecated in v1.0 and will be removed in version 1.2. Use `criterion='squared_error'` which is equivalent.
  warn(
/usr/local/lib/python3.8/dist-packages/sklearn/ensemble/_forest.py:396: FutureWarning: Criterion 'mse' was deprecated in v1.0 and will be removed in version 1.2. Use `criterion='squared_error'` which is equivalent.
  warn(


Iteration: 3


/usr/local/lib/python3.8/dist-packages/sklearn/ensemble/_forest.py:396: FutureWarning: Criterion 'mse' was deprecated in v1.0 and will be removed in version 1.2. Use `criterion='squared_error'` which is equivalent.
  warn(
/usr/local/lib/python3.8/dist-packages/sklearn/ensemble/_forest.py:396: FutureWarning: Criterion 'mse' was deprecated in v1.0 and will be removed in version 1.2. Use `criterion='squared_error'` which is equivalent.
  warn(


Iteration: 0
Iteration: 1
Iteration: 2


/usr/local/lib/python3.8/dist-packages/sklearn/ensemble/_forest.py:396: FutureWarning: Criterion 'mse' was deprecated in v1.0 and will be removed in version 1.2. Use `criterion='squared_error'` which is equivalent.
  warn(


In [49]:
t_start = time.time()
mse_mf30_total = 0 
MSE_MF30_1001 = 0
for i in range(1,1001):
  mse_mf30_total = mse_mf30_total + globals()[f'MSE_MF30_{i}']
AMSE_waist_to_hip_radio3_mf = mse_mf30_total/1000
print(f'AMSE_waist_to_hip_radio3_mf = {AMSE_waist_to_hip_radio3_mf}')
t_end = time.time()
print(f'เวลาที่ใช้ในการประมวลผล {t_end- t_start} วินาที')
print(f'เวลาที่ใช้ในการประมวลผล {(t_end- t_start)/60} นาที')

AMSE_waist_to_hip_radio3_mf = 5.246763906485679e-06
เวลาที่ใช้ในการประมวลผล 0.0011096000671386719 วินาที
เวลาที่ใช้ในการประมวลผล 1.8493334452311197e-05 นาที


## Imputation using the KNN

In [50]:
from sklearn import neighbors
from sklearn.impute import KNNImputer

In [51]:
t_start = time.time()
KNN30_imputer = KNNImputer(n_neighbors = 15)
for i in range(1,1001):
  globals()[f'imputed_KNN30_{i}'] = KNN30_imputer.fit_transform(globals()[f'waist_to_hip_radio3{i}'].copy())
  globals()[f'MSE_KNN30_{i}'] = mean_squared_error(data, globals()[f'imputed_KNN30_{i}'])
t_end = time.time()
t30_KNN = (t_end- t_start)

In [52]:
t_start = time.time()
mse_knn30_total = 0 
MSE_KNN30_1001 = 0
for i in range(1,1001):
  mse_knn30_total = mse_knn30_total + globals()[f'MSE_KNN30_{i}']
AMSE_waist_to_hip_radio3_knn = mse_knn30_total/1000
print(f'AMSE_waist_to_hip_radio3_knn = {AMSE_waist_to_hip_radio3_knn}')
t_end = time.time()
print(f'เวลาที่ใช้ในการประมวลผล {t_end- t_start} วินาที')
print(f'เวลาที่ใช้ในการประมวลผล {(t_end- t_start)/60} นาที')

AMSE_waist_to_hip_radio3_knn = 1.3375260264789685e-05
เวลาที่ใช้ในการประมวลผล 0.0009083747863769531 วินาที
เวลาที่ใช้ในการประมวลผล 1.5139579772949219e-05 นาที


## Imputation using the MICE

In [53]:
from sklearn.experimental import enable_iterative_imputer
from sklearn.impute import IterativeImputer
from sklearn.linear_model import LinearRegression
from sklearn import svm

### LinearRegression model

In [ ]:
t_start = time.time()
lr = LinearRegression()
for i in range(1,1001):
  imp30 = IterativeImputer(estimator= lr , max_iter= 10, verbose=0, imputation_order='roman',initial_strategy = 'mean',random_state= i)
  globals()[f'imputed_lr30_{i}'] = imp30.fit_transform(globals()[f'waist_to_hip_radio3{i}'].copy())
  globals()[f'MSE_lr30_{i}'] = mean_squared_error(data, globals()[f'imputed_lr30_{i}'])
t_end = time.time()
t30_LR = (t_end- t_start)

In [55]:
t_start = time.time()
mse_lr30_total = 0 
MSE_lr30_1001 = 0
for i in range(1,1001):
  mse_lr30_total = mse_lr30_total + globals()[f'MSE_lr30_{i}']
AMSE_waist_to_hip_radio3_lr = mse_lr30_total/1000
print(f'AMSE_waist_to_hip_radio3_lr = {AMSE_waist_to_hip_radio3_lr}')
t_end = time.time()
print(f'เวลาที่ใช้ในการประมวลผล {t_end- t_start} วินาที')
print(f'เวลาที่ใช้ในการประมวลผล {(t_end- t_start)/60} นาที')

AMSE_waist_to_hip_radio3_lr = 1.79022159545036e-05
เวลาที่ใช้ในการประมวลผล 0.000985860824584961 วินาที
เวลาที่ใช้ในการประมวลผล 1.6431013743082683e-05 นาที


### Support Vector Machine model

In [ ]:
t_start = time.time()
regr = svm.SVR()
for i in range(1,1001):
  svm_svr = IterativeImputer(estimator= regr, max_iter= 10, verbose=0, imputation_order='roman',initial_strategy = 'mean',random_state= i)
  globals()[f'imputed_svm30_{i}'] = svm_svr.fit_transform(globals()[f'waist_to_hip_radio3{i}'].copy())
  globals()[f'MSE_svm30_{i}'] = mean_squared_error(data, globals()[f'imputed_svm30_{i}'])
t_end = time.time()
t30_SVM = (t_end- t_start)

In [57]:
t_start = time.time()
mse_svm30_total = 0 
MSE_svm30_1001 = 0
for i in range(1,1001):
  mse_svm30_total = mse_svm30_total + globals()[f'MSE_svm30_{i}']
AMSE_waist_to_hip_radio3_svm = mse_svm30_total/1000
print(f'AMSE_waist_to_hip_radio3_svm = {AMSE_waist_to_hip_radio3_svm}')
t_end = time.time()
print(f'เวลาที่ใช้ในการประมวลผล {t_end- t_start} วินาที')
print(f'เวลาที่ใช้ในการประมวลผล {(t_end- t_start)/60} นาที')

AMSE_waist_to_hip_radio3_svm = 2.6809396850962608e-05
เวลาที่ใช้ในการประมวลผล 0.001003265380859375 วินาที
เวลาที่ใช้ในการประมวลผล 1.6721089680989585e-05 นาที


## Imputation using the EM

### impy.em

In [58]:
!pip install impyute
import impyute as impy

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [59]:
t_start = time.time()
for i in range(1,1001):
  globals()[f'imputed_impy30_{i}'] = impy.em(globals()[f'waist_to_hip_radio3{i}'].values.copy())
  globals()[f'MSE_impy30_{i}'] = mean_squared_error(data, globals()[f'imputed_impy30_{i}'])
t_end = time.time()
t30_EM = (t_end- t_start)

In [60]:
t_start = time.time()
mse_impy30_total = 0 
MSE_impy30_1001 = 0
for i in range(1,1001):
  mse_impy30_total = mse_impy30_total + globals()[f'MSE_impy30_{i}']
AMSE_waist_to_hip_radio3_impy = mse_impy30_total/1000
print(f'AMSE_waist_to_hip_radio3_impy = {AMSE_waist_to_hip_radio3_impy}')
t_end = time.time()
print(f'เวลาที่ใช้ในการประมวลผล {t_end- t_start} วินาที')
print(f'เวลาที่ใช้ในการประมวลผล {(t_end- t_start)/60} นาที')

AMSE_waist_to_hip_radio3_impy = 0.00010116313455188409
เวลาที่ใช้ในการประมวลผล 0.0009737014770507812 วินาที
เวลาที่ใช้ในการประมวลผล 1.6228357950846353e-05 นาที


# 40 % random nan 

In [61]:
for i in range(1,1001):
  globals()[f'waist_to_hip_radio4{i}'] = data.copy() # for loop variable name
  np.random.seed(i) # for loop seed
  n = int((153*40/100)) 
  index_nan = np.random.choice(globals()[f'waist_to_hip_radio4{i}']['waist to hip radio'].size, n, replace=False)
  globals()[f'waist_to_hip_radio4{i}']['waist to hip radio'].ravel()[index_nan] = np.nan

## Imputation using Mean

In [62]:
from sklearn.impute import SimpleImputer

In [63]:
t_start = time.time()
mean40_imputer = SimpleImputer(strategy='mean')
for i in range(1,1001):
  globals()[f'imputed_mean40_{i}'] = mean40_imputer.fit_transform(globals()[f'waist_to_hip_radio4{i}'].copy()) #for loop miss forest impputation 
  globals()[f'MSE_MEAN40_{i}'] = mean_squared_error(data, globals()[f'imputed_mean40_{i}']) # for loop mean_squared_error
t_end = time.time()
t40_MEAN = (t_end- t_start)

In [64]:
t_start = time.time()
mse_mean40_total = 0 
MSE_MEAN40_1001 = 0
for i in range(1,1001):
  mse_mean40_total = mse_mean40_total + globals()[f'MSE_MEAN40_{i}']
AMSE_waist_to_hip_radio4_mean = mse_mean40_total/1000
print(f'AMSE_waist_to_hip_radio4_mean = {AMSE_waist_to_hip_radio4_mean}')
t_end = time.time()
print(f'เวลาที่ใช้ในการประมวลผล {t_end- t_start} วินาที')
print(f'เวลาที่ใช้ในการประมวลผล {(t_end- t_start)/60} นาที')

AMSE_waist_to_hip_radio4_mean = 7.418902289031077e-05
เวลาที่ใช้ในการประมวลผล 0.001161813735961914 วินาที
เวลาที่ใช้ในการประมวลผล 1.93635622660319e-05 นาที


## Imputation using the miss forest

In [65]:
import sys
import sklearn.neighbors._base
sys.modules['sklearn.neighbors.base'] = sklearn.neighbors._base
!pip install missingpy
import missingpy
from missingpy import MissForest
from sklearn.metrics import mean_squared_error

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [66]:
t_start = time.time()
MF40_imputer = MissForest()
for i in range(1,1001):
  globals()[f'imputed_mf40_{i}'] = MF40_imputer.fit_transform(globals()[f'waist_to_hip_radio4{i}'].copy()) #for loop miss forest impputation 
  globals()[f'MSE_MF40_{i}'] = mean_squared_error(data, globals()[f'imputed_mf40_{i}']) # for loop mean_squared_error
t_end = time.time()
t40_MF = (t_end- t_start)

/usr/local/lib/python3.8/dist-packages/sklearn/ensemble/_forest.py:396: FutureWarning: Criterion 'mse' was deprecated in v1.0 and will be removed in version 1.2. Use `criterion='squared_error'` which is equivalent.
  warn(


Iteration: 0


/usr/local/lib/python3.8/dist-packages/sklearn/ensemble/_forest.py:396: FutureWarning: Criterion 'mse' was deprecated in v1.0 and will be removed in version 1.2. Use `criterion='squared_error'` which is equivalent.
  warn(
/usr/local/lib/python3.8/dist-packages/sklearn/ensemble/_forest.py:396: FutureWarning: Criterion 'mse' was deprecated in v1.0 and will be removed in version 1.2. Use `criterion='squared_error'` which is equivalent.
  warn(


Iteration: 1
Iteration: 2


/usr/local/lib/python3.8/dist-packages/sklearn/ensemble/_forest.py:396: FutureWarning: Criterion 'mse' was deprecated in v1.0 and will be removed in version 1.2. Use `criterion='squared_error'` which is equivalent.
  warn(


...

Iteration: 2


/usr/local/lib/python3.8/dist-packages/sklearn/ensemble/_forest.py:396: FutureWarning: Criterion 'mse' was deprecated in v1.0 and will be removed in version 1.2. Use `criterion='squared_error'` which is equivalent.
  warn(


Iteration: 0


/usr/local/lib/python3.8/dist-packages/sklearn/ensemble/_forest.py:396: FutureWarning: Criterion 'mse' was deprecated in v1.0 and will be removed in version 1.2. Use `criterion='squared_error'` which is equivalent.
  warn(
/usr/local/lib/python3.8/dist-packages/sklearn/ensemble/_forest.py:396: FutureWarning: Criterion 'mse' was deprecated in v1.0 and will be removed in version 1.2. Use `criterion='squared_error'` which is equivalent.
  warn(


Iteration: 1
Iteration: 2


In [67]:
t_start = time.time()
mse_mf40_total = 0 
MSE_MF40_1001 = 0
for i in range(1,1001):
  mse_mf40_total = mse_mf40_total + globals()[f'MSE_MF40_{i}']
AMSE_waist_to_hip_radio4_mf = mse_mf40_total/1000
print(f'AMSE_waist_to_hip_radio4_mf = {AMSE_waist_to_hip_radio4_mf}')
t_end = time.time()
print(f'เวลาที่ใช้ในการประมวลผล {t_end- t_start} วินาที')
print(f'เวลาที่ใช้ในการประมวลผล {(t_end- t_start)/60} นาที')

AMSE_waist_to_hip_radio4_mf = 7.301561468074428e-06
เวลาที่ใช้ในการประมวลผล 0.001603841781616211 วินาที
เวลาที่ใช้ในการประมวลผล 2.673069636027018e-05 นาที


## Imputation using the KNN

In [68]:
from sklearn import neighbors
from sklearn.impute import KNNImputer

In [69]:
t_start = time.time()
KNN40_imputer = KNNImputer(n_neighbors = 15)
for i in range(1,1001):
  globals()[f'imputed_KNN40_{i}'] = KNN40_imputer.fit_transform(globals()[f'waist_to_hip_radio4{i}'].copy())
  globals()[f'MSE_KNN40_{i}'] = mean_squared_error(data, globals()[f'imputed_KNN40_{i}'])
t_end = time.time()
t40_KNN = (t_end- t_start)

In [70]:
t_start = time.time()
mse_knn40_total = 0 
MSE_KNN40_1001 = 0
for i in range(1,1001):
  mse_knn40_total = mse_knn40_total + globals()[f'MSE_KNN40_{i}']
AMSE_waist_to_hip_radio4_knn = mse_knn40_total/1000
print(f'AMSE_waist_to_hip_radio4_knn = {AMSE_waist_to_hip_radio4_knn}')
t_end = time.time()
print(f'เวลาที่ใช้ในการประมวลผล {t_end- t_start} วินาที')
print(f'เวลาที่ใช้ในการประมวลผล {(t_end- t_start)/60} นาที')

AMSE_waist_to_hip_radio4_knn = 1.956022691469753e-05
เวลาที่ใช้ในการประมวลผล 0.0009775161743164062 วินาที
เวลาที่ใช้ในการประมวลผล 1.629193623860677e-05 นาที


## Imputation using the MICE

In [71]:
from sklearn.experimental import enable_iterative_imputer
from sklearn.impute import IterativeImputer
from sklearn.linear_model import LinearRegression
from sklearn import svm

### LinearRegression model

In [ ]:
t_start = time.time()
lr = LinearRegression()
for i in range(1,1001):
  imp40 = IterativeImputer(estimator= lr , max_iter= 10, verbose=0, imputation_order='roman',initial_strategy = 'mean',random_state= i)
  globals()[f'imputed_lr40_{i}'] = imp40.fit_transform(globals()[f'waist_to_hip_radio4{i}'].copy())
  globals()[f'MSE_lr40_{i}'] = mean_squared_error(data, globals()[f'imputed_lr40_{i}'])
t_end = time.time()
t40_LR = (t_end- t_start)

In [73]:
t_start = time.time()
mse_lr40_total = 0 
MSE_lr40_1001 = 0
for i in range(1,1001):
  mse_lr40_total = mse_lr40_total + globals()[f'MSE_lr40_{i}']
AMSE_waist_to_hip_radio4_lr = mse_lr40_total/1000
print(f'AMSE_waist_to_hip_radio4_lr = {AMSE_waist_to_hip_radio4_lr}')
t_end = time.time()
print(f'เวลาที่ใช้ในการประมวลผล {t_end- t_start} วินาที')
print(f'เวลาที่ใช้ในการประมวลผล {(t_end- t_start)/60} นาที')

AMSE_waist_to_hip_radio4_lr = 2.84083034622293e-05
เวลาที่ใช้ในการประมวลผล 0.0010161399841308594 วินาที
เวลาที่ใช้ในการประมวลผล 1.693566640218099e-05 นาที


### Support Vector Machine model

In [ ]:
t_start = time.time()
regr = svm.SVR()
for i in range(1,1001):
  svm_svr = IterativeImputer(estimator= regr, max_iter= 10, verbose=0, imputation_order='roman',initial_strategy = 'mean',random_state= i)
  globals()[f'imputed_svm40_{i}'] = svm_svr.fit_transform(globals()[f'waist_to_hip_radio4{i}'].copy())
  globals()[f'MSE_svm40_{i}'] = mean_squared_error(data, globals()[f'imputed_svm40_{i}'])
t_end = time.time()
t40_SVM = (t_end- t_start)

In [75]:
t_start = time.time()
mse_svm40_total = 0 
MSE_svm40_1001 = 0
for i in range(1,1001):
  mse_svm40_total = mse_svm40_total + globals()[f'MSE_svm40_{i}']
AMSE_waist_to_hip_radio4_svm = mse_svm40_total/1000
print(f'AMSE_waist_to_hip_radio4_svm = {AMSE_waist_to_hip_radio4_svm}')
t_end = time.time()
print(f'เวลาที่ใช้ในการประมวลผล {t_end- t_start} วินาที')
print(f'เวลาที่ใช้ในการประมวลผล {(t_end- t_start)/60} นาที')

AMSE_waist_to_hip_radio4_svm = 3.846602460951376e-05
เวลาที่ใช้ในการประมวลผล 0.0009982585906982422 วินาที
เวลาที่ใช้ในการประมวลผล 1.6637643178304036e-05 นาที


## Imputation using the EM

### impy.em

In [76]:
!pip install impyute
import impyute as impy

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [77]:
t_start = time.time()
for i in range(1,1001):
  globals()[f'imputed_impy40_{i}'] = impy.em(globals()[f'waist_to_hip_radio4{i}'].values.copy())
  globals()[f'MSE_impy40_{i}'] = mean_squared_error(data, globals()[f'imputed_impy40_{i}'])
t_end = time.time()
t40_EM = (t_end- t_start)

In [78]:
t_start = time.time()
mse_impy40_total = 0 
MSE_impy40_1001 = 0
for i in range(1,1001):
  mse_impy40_total = mse_impy40_total + globals()[f'MSE_impy40_{i}']
AMSE_waist_to_hip_radio4_impy = mse_impy40_total/1000
print(f'AMSE_waist_to_hip_radio4_impy = {AMSE_waist_to_hip_radio4_impy}')
t_end = time.time()
print(f'เวลาที่ใช้ในการประมวลผล {t_end- t_start} วินาที')
print(f'เวลาที่ใช้ในการประมวลผล {(t_end- t_start)/60} นาที')

AMSE_waist_to_hip_radio4_impy = 0.00013931262812167858
เวลาที่ใช้ในการประมวลผล 0.0013625621795654297 วินาที
เวลาที่ใช้ในการประมวลผล 2.2709369659423828e-05 นาที


# 50 % random nan 

In [79]:
for i in range(1,1001):
  globals()[f'waist_to_hip_radio5{i}'] = data.copy() # for loop variable name
  np.random.seed(i) # for loop seed
  n = int((153*50/100)) 
  index_nan = np.random.choice(globals()[f'waist_to_hip_radio5{i}']['waist to hip radio'].size, n, replace=False)
  globals()[f'waist_to_hip_radio5{i}']['waist to hip radio'].ravel()[index_nan] = np.nan

## Imputation using Mean

In [80]:
from sklearn.impute import SimpleImputer

In [81]:
t_start = time.time()
mean50_imputer = SimpleImputer(strategy='mean')
for i in range(1,1001):
  globals()[f'imputed_mean50_{i}'] = mean50_imputer.fit_transform(globals()[f'waist_to_hip_radio5{i}'].copy()) #for loop miss forest impputation 
  globals()[f'MSE_MEAN50_{i}'] = mean_squared_error(data, globals()[f'imputed_mean50_{i}']) # for loop mean_squared_error
t_end = time.time()
t50_MEAN = (t_end- t_start)

In [82]:
t_start = time.time()
mse_mean50_total = 0 
MSE_MEAN50_1001 = 0
for i in range(1,1001):
  mse_mean50_total = mse_mean50_total + globals()[f'MSE_MEAN50_{i}']
AMSE_waist_to_hip_radio5_mean = mse_mean50_total/1000
print(f'AMSE_waist_to_hip_radio5_mean = {AMSE_waist_to_hip_radio5_mean}')
t_end = time.time()
print(f'เวลาที่ใช้ในการประมวลผล {t_end- t_start} วินาที')
print(f'เวลาที่ใช้ในการประมวลผล {(t_end- t_start)/60} นาที')

AMSE_waist_to_hip_radio5_mean = 9.271041633012613e-05
เวลาที่ใช้ในการประมวลผล 0.0010347366333007812 วินาที
เวลาที่ใช้ในการประมวลผล 1.724561055501302e-05 นาที


## Imputation using the miss forest

In [83]:
import sys
import sklearn.neighbors._base
sys.modules['sklearn.neighbors.base'] = sklearn.neighbors._base
!pip install missingpy
import missingpy
from missingpy import MissForest
from sklearn.metrics import mean_squared_error

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [84]:
t_start = time.time()
MF50_imputer = MissForest()
for i in range(1,1001):
  globals()[f'imputed_mf50_{i}'] = MF50_imputer.fit_transform(globals()[f'waist_to_hip_radio5{i}'].copy()) #for loop miss forest impputation 
  globals()[f'MSE_MF50_{i}'] = mean_squared_error(data, globals()[f'imputed_mf50_{i}']) # for loop mean_squared_error
t_end = time.time()
t50_MF = (t_end- t_start)

/usr/local/lib/python3.8/dist-packages/sklearn/ensemble/_forest.py:396: FutureWarning: Criterion 'mse' was deprecated in v1.0 and will be removed in version 1.2. Use `criterion='squared_error'` which is equivalent.
  warn(
/usr/local/lib/python3.8/dist-packages/sklearn/ensemble/_forest.py:396: FutureWarning: Criterion 'mse' was deprecated in v1.0 and will be removed in version 1.2. Use `criterion='squared_error'` which is equivalent.
  warn(


Iteration: 0
Iteration: 1


/usr/local/lib/python3.8/dist-packages/sklearn/ensemble/_forest.py:396: FutureWarning: Criterion 'mse' was deprecated in v1.0 and will be removed in version 1.2. Use `criterion='squared_error'` which is equivalent.
  warn(


Iteration: 2
Iteration: 3


/usr/local/lib/python3.8/dist-packages/sklearn/ensemble/_forest.py:396: FutureWarning: Criterion 'mse' was deprecated in v1.0 and will be removed in version 1.2. Use `criterion='squared_error'` which is equivalent.
  warn(
/usr/local/lib/python3.8/dist-packages/sklearn/ensemble/_forest.py:396: FutureWarning: Criterion 'mse' was deprecated in v1.0 and will be removed in version 1.2. Use `criterion='squared_error'` which is equivalent.
  warn(


...

Iteration: 2


/usr/local/lib/python3.8/dist-packages/sklearn/ensemble/_forest.py:396: FutureWarning: Criterion 'mse' was deprecated in v1.0 and will be removed in version 1.2. Use `criterion='squared_error'` which is equivalent.
  warn(
/usr/local/lib/python3.8/dist-packages/sklearn/ensemble/_forest.py:396: FutureWarning: Criterion 'mse' was deprecated in v1.0 and will be removed in version 1.2. Use `criterion='squared_error'` which is equivalent.
  warn(


Iteration: 0
Iteration: 1


/usr/local/lib/python3.8/dist-packages/sklearn/ensemble/_forest.py:396: FutureWarning: Criterion 'mse' was deprecated in v1.0 and will be removed in version 1.2. Use `criterion='squared_error'` which is equivalent.
  warn(
/usr/local/lib/python3.8/dist-packages/sklearn/ensemble/_forest.py:396: FutureWarning: Criterion 'mse' was deprecated in v1.0 and will be removed in version 1.2. Use `criterion='squared_error'` which is equivalent.
  warn(


Iteration: 2
Iteration: 3


In [85]:
t_start = time.time()
mse_mf50_total = 0 
MSE_MF50_1001 = 0
for i in range(0,1001):
  mse_mf50_total = mse_mf50_total + globals()[f'MSE_MF50_{i+1}']
AMSE_waist_to_hip_radio5_mf = mse_mf50_total/1000
print(f'AMSE_waist_to_hip_radio5_mf = {AMSE_waist_to_hip_radio5_mf}')
t_end = time.time()
print(f'เวลาที่ใช้ในการประมวลผล {t_end- t_start} วินาที')
print(f'เวลาที่ใช้ในการประมวลผล {(t_end- t_start)/60} นาที')

AMSE_waist_to_hip_radio5_mf = 9.376279379084982e-06
เวลาที่ใช้ในการประมวลผล 0.0014765262603759766 วินาที
เวลาที่ใช้ในการประมวลผล 2.4608771006266276e-05 นาที


## Imputation using the KNN

In [86]:
from sklearn import neighbors
from sklearn.impute import KNNImputer

In [87]:
t_start = time.time()
KNN50_imputer = KNNImputer(n_neighbors = 15)
for i in range(1,1001):
  globals()[f'imputed_KNN50_{i}'] = KNN30_imputer.fit_transform(globals()[f'waist_to_hip_radio5{i}'].copy())
  globals()[f'MSE_KNN50_{i}'] = mean_squared_error(data, globals()[f'imputed_KNN50_{i}'])
t_end = time.time()
t50_KNN = (t_end- t_start)

In [88]:
t_start = time.time()
mse_knn50_total = 0 
MSE_KNN50_1001 = 0
for i in range(1,1001):
  mse_knn50_total = mse_knn30_total + globals()[f'MSE_KNN50_{i}']
AMSE_waist_to_hip_radio5_knn = mse_knn30_total/1000
print(f'AMSE_waist_to_hip_radio5_knn = {AMSE_waist_to_hip_radio5_knn}')
t_end = time.time()
print(f'เวลาที่ใช้ในการประมวลผล {t_end- t_start} วินาที')
print(f'เวลาที่ใช้ในการประมวลผล {(t_end- t_start)/60} นาที')

AMSE_waist_to_hip_radio5_knn = 1.3375260264789685e-05
เวลาที่ใช้ในการประมวลผล 0.0015363693237304688 วินาที
เวลาที่ใช้ในการประมวลผล 2.5606155395507814e-05 นาที


## Imputation using the MICE

In [89]:
from sklearn.experimental import enable_iterative_imputer
from sklearn.impute import IterativeImputer
from sklearn.linear_model import LinearRegression
from sklearn import svm

### LinearRegression model

In [ ]:
t_start = time.time()
lr = LinearRegression()
for i in range(1,1001):
  imp50 = IterativeImputer(estimator= lr , max_iter= 10, verbose=0, imputation_order='roman',initial_strategy = 'mean',random_state= i)
  globals()[f'imputed_lr50_{i}'] = imp50.fit_transform(globals()[f'waist_to_hip_radio5{i}'].copy())
  globals()[f'MSE_lr50_{i}'] = mean_squared_error(data, globals()[f'imputed_lr50_{i}'])
t_end = time.time()
t50_LR = (t_end- t_start)

In [91]:
t_start = time.time()
mse_lr50_total = 0 
MSE_lr50_1001 = 0
for i in range(1,1001):
  mse_lr50_total = mse_lr50_total + globals()[f'MSE_lr50_{i}']
AMSE_waist_to_hip_radio5_lr = mse_lr50_total/1000
print(f'AMSE_waist_to_hip_radio5_lr = {AMSE_waist_to_hip_radio5_lr}')
t_end = time.time()
print(f'เวลาที่ใช้ในการประมวลผล {t_end- t_start} วินาที')
print(f'เวลาที่ใช้ในการประมวลผล {(t_end- t_start)/60} นาที')

AMSE_waist_to_hip_radio5_lr = 4.3883017895758477e-05
เวลาที่ใช้ในการประมวลผล 0.0010275840759277344 วินาที
เวลาที่ใช้ในการประมวลผล 1.712640126546224e-05 นาที


### Support Vector Machine model

In [ ]:
t_start = time.time()
regr = svm.SVR()
for i in range(1,1001):
  svm_svr = IterativeImputer(estimator= regr, max_iter= 10, verbose=2, imputation_order='roman',initial_strategy = 'mean',random_state= i)
  globals()[f'imputed_svm50_{i}'] = svm_svr.fit_transform(globals()[f'waist_to_hip_radio5{i}'].copy())
  globals()[f'MSE_svm50_{i}'] = mean_squared_error(data, globals()[f'imputed_svm50_{i}'])
t_end = time.time()
t50_SVM = (t_end- t_start)

In [93]:
t_start = time.time()
mse_svm50_total = 0 
MSE_svm50_1001 = 0
for i in range(1,1001):
  mse_svm50_total = mse_svm50_total + globals()[f'MSE_svm50_{i}']
AMSE_waist_to_hip_radio5_svm = mse_svm50_total/1000
print(f'AMSE_waist_to_hip_radio5_svm = {AMSE_waist_to_hip_radio5_svm}')
t_end = time.time()
print(f'เวลาที่ใช้ในการประมวลผล {t_end- t_start} วินาที')
print(f'เวลาที่ใช้ในการประมวลผล {(t_end- t_start)/60} นาที')

AMSE_waist_to_hip_radio5_svm = 5.075715662685119e-05
เวลาที่ใช้ในการประมวลผล 0.001062631607055664 วินาที
เวลาที่ใช้ในการประมวลผล 1.7710526784261067e-05 นาที


## Imputation using the EM

### impy.em

In [94]:
!pip install impyute
import impyute as impy

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [95]:
t_start = time.time()
for i in range(1,1001):
  globals()[f'imputed_impy50_{i}'] = impy.em(globals()[f'waist_to_hip_radio5{i}'].values.copy())
  globals()[f'MSE_impy50_{i}'] = mean_squared_error(data, globals()[f'imputed_impy50_{i}'])
t_end = time.time()
t50_EM = (t_end- t_start)

In [96]:
t_start = time.time()
mse_impy50_total = 0 
MSE_impy50_1001 = 0
for i in range(1,1001):
  mse_impy50_total = mse_impy50_total + globals()[f'MSE_impy50_{i}']
AMSE_waist_to_hip_radio5_impy = mse_impy50_total/1000
print(f'AMSE_waist_to_hip_radio5_impy = {AMSE_waist_to_hip_radio5_impy}')
t_end = time.time()
print(f'เวลาที่ใช้ในการประมวลผล {t_end- t_start} วินาที')
print(f'เวลาที่ใช้ในการประมวลผล {(t_end- t_start)/60} นาที')

AMSE_waist_to_hip_radio5_impy = 0.00017345549251708081
เวลาที่ใช้ในการประมวลผล 0.0010023117065429688 วินาที
เวลาที่ใช้ในการประมวลผล 1.6705195109049478e-05 นาที


# 60 % random nan 

In [97]:
for i in range(1,1001):
  globals()[f'waist_to_hip_radio6{i}'] = data.copy() # for loop variable name
  np.random.seed(i) # for loop seed
  n = int((153*60/100)) 
  index_nan = np.random.choice(globals()[f'waist_to_hip_radio6{i}']['waist to hip radio'].size, n, replace=False)
  globals()[f'waist_to_hip_radio6{i}']['waist to hip radio'].ravel()[index_nan] = np.nan

## Imputation using Mean

In [98]:
from sklearn.impute import SimpleImputer

In [99]:
t_start = time.time()
mean60_imputer = SimpleImputer(strategy='mean')
for i in range(1,1001):
  globals()[f'imputed_mean60_{i}'] = mean60_imputer.fit_transform(globals()[f'waist_to_hip_radio6{i}'].copy()) #for loop miss forest impputation 
  globals()[f'MSE_MEAN60_{i}'] = mean_squared_error(data, globals()[f'imputed_mean60_{i}']) # for loop mean_squared_error
t_end = time.time()
t60_MEAN = (t_end- t_start)

In [100]:
t_start = time.time()
mse_mean60_total = 0 
MSE_MEAN60_1001 = 0
for i in range(1,1001):
  mse_mean60_total = mse_mean60_total + globals()[f'MSE_MEAN60_{i}']
AMSE_waist_to_hip_radio6_mean = mse_mean60_total/1000
print(f'AMSE_waist_to_hip_radio6_mean = {AMSE_waist_to_hip_radio6_mean}')
t_end = time.time()
print(f'เวลาที่ใช้ในการประมวลผล {t_end- t_start} วินาที')
print(f'เวลาที่ใช้ในการประมวลผล {(t_end- t_start)/60} นาที')

AMSE_waist_to_hip_radio6_mean = 0.00011142407833353998
เวลาที่ใช้ในการประมวลผล 0.0015273094177246094 วินาที
เวลาที่ใช้ในการประมวลผล 2.5455156962076823e-05 นาที


## Imputation using the miss forest

In [101]:
import sys
import sklearn.neighbors._base
sys.modules['sklearn.neighbors.base'] = sklearn.neighbors._base
!pip install missingpy
import missingpy
from missingpy import MissForest
from sklearn.metrics import mean_squared_error

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [102]:
t_start = time.time()
MF60_imputer = MissForest()
for i in range(1,1001):
  globals()[f'imputed_mf60_{i}'] = MF60_imputer.fit_transform(globals()[f'waist_to_hip_radio6{i}'].copy()) #for loop miss forest impputation 
  globals()[f'MSE_MF60_{i}'] = mean_squared_error(data, globals()[f'imputed_mf60_{i}']) # for loop mean_squared_error
t_end = time.time()
t60_MF = (t_end- t_start)

/usr/local/lib/python3.8/dist-packages/sklearn/ensemble/_forest.py:396: FutureWarning: Criterion 'mse' was deprecated in v1.0 and will be removed in version 1.2. Use `criterion='squared_error'` which is equivalent.
  warn(


Iteration: 0


/usr/local/lib/python3.8/dist-packages/sklearn/ensemble/_forest.py:396: FutureWarning: Criterion 'mse' was deprecated in v1.0 and will be removed in version 1.2. Use `criterion='squared_error'` which is equivalent.
  warn(
/usr/local/lib/python3.8/dist-packages/sklearn/ensemble/_forest.py:396: FutureWarning: Criterion 'mse' was deprecated in v1.0 and will be removed in version 1.2. Use `criterion='squared_error'` which is equivalent.
  warn(


Iteration: 1
Iteration: 2


/usr/local/lib/python3.8/dist-packages/sklearn/ensemble/_forest.py:396: FutureWarning: Criterion 'mse' was deprecated in v1.0 and will be removed in version 1.2. Use `criterion='squared_error'` which is equivalent.
  warn(
/usr/local/lib/python3.8/dist-packages/sklearn/ensemble/_forest.py:396: FutureWarning: Criterion 'mse' was deprecated in v1.0 and will be removed in version 1.2. Use `criterion='squared_error'` which is equivalent.
  warn(


...

Iteration: 2


/usr/local/lib/python3.8/dist-packages/sklearn/ensemble/_forest.py:396: FutureWarning: Criterion 'mse' was deprecated in v1.0 and will be removed in version 1.2. Use `criterion='squared_error'` which is equivalent.
  warn(


Iteration: 0
Iteration: 1


/usr/local/lib/python3.8/dist-packages/sklearn/ensemble/_forest.py:396: FutureWarning: Criterion 'mse' was deprecated in v1.0 and will be removed in version 1.2. Use `criterion='squared_error'` which is equivalent.
  warn(
/usr/local/lib/python3.8/dist-packages/sklearn/ensemble/_forest.py:396: FutureWarning: Criterion 'mse' was deprecated in v1.0 and will be removed in version 1.2. Use `criterion='squared_error'` which is equivalent.
  warn(


Iteration: 2


In [103]:
t_start = time.time()
mse_mf60_total = 0 
MSE_MF60_1001 = 0
for i in range(1,1001):
  mse_mf60_total = mse_mf60_total + globals()[f'MSE_MF60_{i}']
AMSE_waist_to_hip_radio6_mf = mse_mf60_total/1000
print(f'AMSE_waist_to_hip_radio6_mf = {AMSE_waist_to_hip_radio6_mf}')
t_end = time.time()
print(f'เวลาที่ใช้ในการประมวลผล {t_end- t_start} วินาที')
print(f'เวลาที่ใช้ในการประมวลผล {(t_end- t_start)/60} นาที')

AMSE_waist_to_hip_radio6_mf = 1.2026897169431887e-05
เวลาที่ใช้ในการประมวลผล 0.0011150836944580078 วินาที
เวลาที่ใช้ในการประมวลผล 1.8584728240966798e-05 นาที


## Imputation using the KNN

In [104]:
from sklearn import neighbors
from sklearn.impute import KNNImputer

In [105]:
t_start = time.time()
KNN60_imputer = KNNImputer(n_neighbors = 15)
for i in range(1,1001):
  globals()[f'imputed_KNN60_{i}'] = KNN60_imputer.fit_transform(globals()[f'waist_to_hip_radio6{i}'].copy())
  globals()[f'MSE_KNN60_{i}'] = mean_squared_error(data, globals()[f'imputed_KNN60_{i}'])
t_end = time.time()
t60_KNN = (t_end- t_start)

In [106]:
t_start = time.time()
mse_knn60_total = 0 
MSE_KNN60_1001 = 0
for i in range(1,1001):
  mse_knn60_total = mse_knn60_total + globals()[f'MSE_KNN60_{i}']
AMSE_waist_to_hip_radio6_knn = mse_knn60_total/1000
print(f'AMSE_waist_to_hip_radio6_knn = {AMSE_waist_to_hip_radio6_knn}')
t_end = time.time()
print(f'เวลาที่ใช้ในการประมวลผล {t_end- t_start} วินาที')
print(f'เวลาที่ใช้ในการประมวลผล {(t_end- t_start)/60} นาที')

AMSE_waist_to_hip_radio6_knn = 3.640076073962351e-05
เวลาที่ใช้ในการประมวลผล 0.0023660659790039062 วินาที
เวลาที่ใช้ในการประมวลผล 3.943443298339844e-05 นาที


## Imputation using the MICE

In [107]:
from sklearn.experimental import enable_iterative_imputer
from sklearn.impute import IterativeImputer
from sklearn.linear_model import LinearRegression
from sklearn import svm

### LinearRegression model

In [ ]:
t_start = time.time()
lr = LinearRegression()
for i in range(1,1001):
  imp60 = IterativeImputer(estimator= lr , max_iter= 10, verbose=0, imputation_order='roman',initial_strategy = 'mean',random_state= i)
  globals()[f'imputed_lr60_{i}'] = imp60.fit_transform(globals()[f'waist_to_hip_radio6{i}'].copy())
  globals()[f'MSE_lr60_{i}'] = mean_squared_error(data, globals()[f'imputed_lr60_{i}'])
t_end = time.time()
t60_LR = (t_end- t_start)

In [109]:
t_start = time.time()
mse_lr60_total = 0 
MSE_lr60_1001 = 0
for i in range(1,1001):
  mse_lr60_total = mse_lr60_total + globals()[f'MSE_lr60_{i}']
AMSE_waist_to_hip_radio6_lr = mse_lr60_total/1000
print(f'AMSE_waist_to_hip_radio6_lr = {AMSE_waist_to_hip_radio6_lr}')
t_end = time.time()
print(f'เวลาที่ใช้ในการประมวลผล {t_end- t_start} วินาที')
print(f'เวลาที่ใช้ในการประมวลผล {(t_end- t_start)/60} นาที')

AMSE_waist_to_hip_radio6_lr = 7.571320202572006e-05
เวลาที่ใช้ในการประมวลผล 0.0010025501251220703 วินาที
เวลาที่ใช้ในการประมวลผล 1.6709168752034504e-05 นาที


### Support Vector Machine model

In [ ]:
t_start = time.time()
regr = svm.SVR()
for i in range(1,1001):
  svm_svr = IterativeImputer(estimator= regr, max_iter= 10, verbose=2, imputation_order='roman',initial_strategy = 'mean',random_state= i)
  globals()[f'imputed_svm60_{i}'] = svm_svr.fit_transform(globals()[f'waist_to_hip_radio6{i}'].copy())
  globals()[f'MSE_svm60_{i}'] = mean_squared_error(data, globals()[f'imputed_svm60_{i}'])
t_end = time.time()
t60_SVM = (t_end- t_start)

In [111]:
t_start = time.time()
mse_svm60_total = 0 
MSE_svm60_1001 = 0
for i in range(1,1001):
  mse_svm60_total = mse_svm60_total + globals()[f'MSE_svm60_{i}']
AMSE_waist_to_hip_radio6_svm = mse_svm60_total/1000
print(f'AMSE_waist_to_hip_radio6_svm = {AMSE_waist_to_hip_radio6_svm}')
t_end = time.time()
print(f'เวลาที่ใช้ในการประมวลผล {t_end- t_start} วินาที')
print(f'เวลาที่ใช้ในการประมวลผล {(t_end- t_start)/60} นาที')

AMSE_waist_to_hip_radio6_svm = 6.557783057266272e-05
เวลาที่ใช้ในการประมวลผล 0.0009951591491699219 วินาที
เวลาที่ใช้ในการประมวลผล 1.6585985819498697e-05 นาที


## Imputation using the EM

### impy.em

In [112]:
!pip install impyute
import impyute as impy

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [113]:
t_start = time.time()
for i in range(1,1001):
  globals()[f'imputed_impy60_{i}'] = impy.em(globals()[f'waist_to_hip_radio6{i}'].values.copy())
  globals()[f'MSE_impy60_{i}'] = mean_squared_error(data, globals()[f'imputed_impy60_{i}'])
t_end = time.time()
t60_EM = (t_end- t_start)

In [114]:
t_start = time.time()
mse_impy60_total = 0 
MSE_impy60_1001 = 0
for i in range(1,1001):
  mse_impy60_total = mse_impy60_total + globals()[f'MSE_impy60_{i}']
AMSE_waist_to_hip_radio6_impy = mse_impy60_total/1000
print(f'AMSE_waist_to_hip_radio6_impy = {AMSE_waist_to_hip_radio6_impy}')
t_end = time.time()
print(f'เวลาที่ใช้ในการประมวลผล {t_end- t_start} วินาที')
print(f'เวลาที่ใช้ในการประมวลผล {(t_end- t_start)/60} นาที')

AMSE_waist_to_hip_radio6_impy = 0.0002070359520517096
เวลาที่ใช้ในการประมวลผล 0.0012784004211425781 วินาที
เวลาที่ใช้ในการประมวลผล 2.1306673685709634e-05 นาที


# AMSE

In [115]:
amse_value = {'Method':['MEAN','Miss Forest','KNN','MICE-LR','MICE-SVM','EM'],
              '10%':[AMSE_waist_to_hip_radio1_mean,AMSE_waist_to_hip_radio1_mf,AMSE_waist_to_hip_radio1_knn,AMSE_waist_to_hip_radio1_lr,AMSE_waist_to_hip_radio1_svm,AMSE_waist_to_hip_radio1_impy],
      '20%':[AMSE_waist_to_hip_radio2_mean,AMSE_waist_to_hip_radio2_mf,AMSE_waist_to_hip_radio2_knn,AMSE_waist_to_hip_radio2_lr,AMSE_waist_to_hip_radio2_svm,AMSE_waist_to_hip_radio2_impy],
      '30%':[AMSE_waist_to_hip_radio3_mean,AMSE_waist_to_hip_radio3_mf,AMSE_waist_to_hip_radio3_knn,AMSE_waist_to_hip_radio3_lr,AMSE_waist_to_hip_radio3_svm,AMSE_waist_to_hip_radio3_impy],
      '40%':[AMSE_waist_to_hip_radio4_mean,AMSE_waist_to_hip_radio4_mf,AMSE_waist_to_hip_radio4_knn,AMSE_waist_to_hip_radio4_lr,AMSE_waist_to_hip_radio4_svm,AMSE_waist_to_hip_radio4_impy],
      '50%':[AMSE_waist_to_hip_radio5_mean,AMSE_waist_to_hip_radio5_mf,AMSE_waist_to_hip_radio5_knn,AMSE_waist_to_hip_radio5_lr,AMSE_waist_to_hip_radio5_svm,AMSE_waist_to_hip_radio5_impy]
      ,'60%':[AMSE_waist_to_hip_radio6_mean,AMSE_waist_to_hip_radio6_mf,AMSE_waist_to_hip_radio6_knn,AMSE_waist_to_hip_radio6_lr,AMSE_waist_to_hip_radio6_svm,AMSE_waist_to_hip_radio6_impy]}

In [116]:
data_AMSE = pd.DataFrame.from_dict(amse_value)
data_AMSE

Method       10%       20%       30%       40%       50%       60%
0         MEAN  0.000018  0.000036  0.000054  0.000074  0.000093  0.000111
1  Miss Forest  0.000002  0.000003  0.000005  0.000007  0.000009  0.000012
2          KNN  0.000004  0.000008  0.000013  0.000020  0.000013  0.000036
3      MICE-LR  0.000004  0.000010  0.000018  0.000028  0.000044  0.000076
4     MICE-SVM  0.000008  0.000017  0.000027  0.000038  0.000051  0.000066
5           EM  0.000034  0.000068  0.000101  0.000139  0.000173  0.000207

# เวลาทั้งหมดในการรัน

## second 

In [117]:
data_t_sec = {'Method':['MEAN','Miss Forest','KNN','MICE-LR','MICE-SVM','EM'],'10%':[t10_MEAN,t10_MF,t10_KNN,t10_LR,t10_SVM,t10_EM],
      '20%':[t20_MEAN,t20_MF,t20_KNN,t20_LR,t20_SVM,t20_EM],'30%':[t30_MEAN,t30_MF,t30_KNN,t30_LR,t30_SVM,t30_EM],'40%':[t40_MEAN,t40_MF,t40_KNN,t40_LR,t40_SVM,t40_EM],
      '50%':[t50_MEAN,t50_MF,t50_KNN,t50_LR,t50_SVM,t50_EM],'60%':[t60_MEAN,t60_MF,t60_KNN,t60_LR,t60_SVM,t60_EM]}

In [118]:
data_second = pd.DataFrame.from_dict(data_t_sec)
data_second

Method         10%         20%         30%         40%         50%  \
0         MEAN    4.167680    4.178836    4.341943    4.366338    4.430305   
1  Miss Forest  772.937013  773.266135  782.713632  787.403701  783.030316   
2          KNN    5.081511    5.339199    5.584346    5.932073    9.772233   
3      MICE-LR   33.479150   36.743804   38.413032   41.387473   43.434317   
4     MICE-SVM   65.929542   67.401159   68.163355   68.332536   68.904947   
5           EM    7.224746   12.542269   17.602421   23.372362   28.614252   

          60%  
0    4.417061  
1  775.506403  
2    9.968225  
3   46.732287  
4   69.608394  
5   34.013044

## minutes

In [119]:
data_t_min = {'Method':['MEAN','Miss Forest','KNN','MICE-LR','MICE-SVM','EM'],'10%':[t10_MEAN/60,t10_MF/60,t10_KNN/60,t10_LR/60,t10_SVM/60,t10_EM/60],
      '20%':[t20_MEAN/60,t20_MF/60,t20_KNN/60,t20_LR/60,t20_SVM/60,t20_EM/60],'30%':[t30_MEAN/60,t30_MF/60,t30_KNN/60,t30_LR/60,t30_SVM/60,t30_EM/60]
      ,'40%':[t40_MEAN/60,t40_MF/60,t40_KNN/60,t40_LR/60,t40_SVM/60,t40_EM/60],'50%':[t50_MEAN/60,t50_MF/60,t50_KNN/60,t50_LR/60,t50_SVM/60,t50_EM/60],
      '60%':[t60_MEAN/60,t60_MF/60,t60_KNN/60,t60_LR/60,t60_SVM/60,t60_EM/60]}

In [120]:
data_minutes = pd.DataFrame.from_dict(data_t_min)
data_minutes

Method        10%        20%        30%        40%        50%  \
0         MEAN   0.069461   0.069647   0.072366   0.072772   0.073838   
1  Miss Forest  12.882284  12.887769  13.045227  13.123395  13.050505   
2          KNN   0.084692   0.088987   0.093072   0.098868   0.162871   
3      MICE-LR   0.557986   0.612397   0.640217   0.689791   0.723905   
4     MICE-SVM   1.098826   1.123353   1.136056   1.138876   1.148416   
5           EM   0.120412   0.209038   0.293374   0.389539   0.476904   

         60%  
0   0.073618  
1  12.925107  
2   0.166137  
3   0.778871  
4   1.160140  
5   0.566884